## XGB model
This notebooks trains the XGBoost model required for the experiment.

Best, use this docker image because everything else is crazy incompatible.

```docker pull onnx/onnx-ecosystem```

https://github.com/onnx/onnx-docker


In [1]:
import os
import pandas as pd
import glob

In [2]:
#!pip3 install xgboost sklearn

In [4]:
#!pip3 install mc2cgen

In [5]:
# first, prep data

In [6]:
# scratch_dir = '/hot/scratch/xgb_flights/'
# flights_root = '/hot/data/flights_all/'

scratch_dir = '/Users/leonhards/Downloads/scratch/xgb_flights/'
flights_root = '/Users/leonhards/Downloads/flights/'

In [7]:
paths = glob.glob(os.path.join(flights_root, 'flights_on_time*.csv'))

In [8]:
target_vars = ['ARR_DELAY', 'DEP_DELAY', 'CARRIER_DELAY',
               'WEATHER_DELAY', 'NAS_DELAY', 'SECURITY_DELAY',
               'LATE_AIRCRAFT_DELAY']

In [9]:
decision_vars = ['QUARTER', 'MONTH', 'DAY_OF_MONTH', 'DAY_OF_WEEK',
                 'OP_UNIQUE_CARRIER', 'ORIGIN_AIRPORT_ID', 'DEST_AIRPORT_ID',
                 'DISTANCE', 'CRS_ARR_TIME', 'CRS_DEP_TIME', 'OP_CARRIER_FL_NUM']

In [10]:
# use years with data! 2003 and june!

In [11]:
paths

['/Users/leonhards/Downloads/flights/flights_on_time_performance_2019_01.csv']

In [12]:
path = paths[0]
def has_data(path):
    year, month = int(path[path.find('mance_')+6:-7]), int(path[path.find('mance_')+11:-4])
    if year > 2003:
        return True
    return year == 2003 and month >= 6

In [13]:
paths_with_data = sorted(list(filter(has_data, paths)))

In [14]:
path = paths_with_data[0]

In [15]:
df = pd.read_csv(path)

/usr/local/lib/python3.9/site-packages/ipython-7.28.0-py3.9.egg/IPython/core/interactiveshell.py:3444: DtypeWarning: Columns (77,84,85) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [16]:
len(df)

583985

In [17]:
valid_idx = df[target_vars].dropna().index

In [18]:
df = df.loc[valid_idx]
len(df)

105222

In [19]:
# remove diverted and cancelled flights. => they get special treatment.
len(df[(df['DIVERTED'] != 1.0) & (df['CANCELLED'] != 1.0)])

105222

In [20]:
# filter out to what is only needed
dest_preprocess_dir = os.path.join(scratch_dir, 'prefiltered')
os.makedirs(dest_preprocess_dir, exist_ok=True)

In [21]:
from tqdm import tqdm

In [22]:
# preprocess csv files and write out!
for path in tqdm(paths_with_data[:2]):
    df = pd.read_csv(path, usecols=target_vars + decision_vars)
    
    valid_idx = df[target_vars].dropna().index
    df = df.loc[valid_idx]
    df.to_csv(os.path.join(dest_preprocess_dir, os.path.basename(path)), index=None)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:03<00:00,  3.22s/it]


In [23]:
# load a single file and make an XGB boost out of it!
paths = sorted(glob.glob(os.path.join(dest_preprocess_dir, 'flights_on_*.csv')))

path = paths[0]

In [24]:
df = pd.read_csv(path)

In [25]:
categorical_vars = ['OP_UNIQUE_CARRIER', 'ORIGIN_AIRPORT_ID', 'DEST_AIRPORT_ID', 'OP_CARRIER_FL_NUM']

In [26]:
df[df['ARR_DELAY'] > 0.0]

QUARTER  MONTH  DAY_OF_MONTH  DAY_OF_WEEK OP_UNIQUE_CARRIER  \
0             1      1             3            4                9E   
1             1      1             4            5                9E   
2             1      1            11            5                9E   
3             1      1            15            2                9E   
4             1      1            19            6                9E   
...         ...    ...           ...          ...               ...   
105217        1      1            20            7                UA   
105218        1      1            20            7                UA   
105219        1      1            20            7                UA   
105220        1      1            20            7                UA   
105221        1      1            20            7                UA   

        OP_CARRIER_FL_NUM  ORIGIN_AIRPORT_ID  DEST_AIRPORT_ID  CRS_DEP_TIME  \
0                    5121              15412            10397          1140   
1                    5121              15412            10397          1140   
2                    5122              10397            14783           950   
3                    5122              10397            14783           950   
4                    5122              10397            14783           950   
...                   ...                ...              ...           ...   
105217                590              14635            12266          1400   
105218                583              13303            14771          1802   
105219                576              11292            11618           945   
105220                569              14057            14771          1327   
105221                560              12264            14771          1736   

        DEP_DELAY  CRS_ARR_TIME  ARR_DELAY  DISTANCE  CARRIER_DELAY  \
0            25.0          1250       25.0     152.0            0.0   
1            70.0          1250       82.0     152.0            0.0   
2            -5.0          1053       20.0     563.0            0.0   
3            53.0          1053       43.0     563.0           11.0   
4            11.0          1051       22.0     563.0            0.0   
...           ...           ...        ...       ...            ...   
105217       80.0          1538       69.0     861.0            0.0   
105218       15.0          2133       23.0    2585.0           15.0   
105219       52.0          1530       47.0    1605.0            0.0   
105220       61.0          1515       49.0     550.0            0.0   
105221       -1.0          2030       23.0    2419.0            0.0   

        WEATHER_DELAY  NAS_DELAY  SECURITY_DELAY  LATE_AIRCRAFT_DELAY  
0                 0.0        0.0             0.0                 25.0  
1                 0.0       12.0             0.0                 70.0  
2                 0.0       20.0             0.0                  0.0  
3                 0.0        0.0             0.0                 32.0  
4                 0.0       11.0             0.0                 11.0  
...               ...        ...             ...                  ...  
105217            0.0        0.0             0.0                 69.0  
105218            0.0        8.0             0.0                  0.0  
105219            0.0       47.0             0.0                  0.0  
105220            0.0        0.0             0.0                 49.0  
105221            0.0       23.0             0.0                  0.0  

[105222 rows x 18 columns]

In [27]:
df_encoded = pd.get_dummies(df, columns=categorical_vars, sparse=True)

In [28]:
df_encoded.columns

Index(['QUARTER', 'MONTH', 'DAY_OF_MONTH', 'DAY_OF_WEEK', 'CRS_DEP_TIME',
       'DEP_DELAY', 'CRS_ARR_TIME', 'ARR_DELAY', 'DISTANCE', 'CARRIER_DELAY',
       ...
       'OP_CARRIER_FL_NUM_7429', 'OP_CARRIER_FL_NUM_7430',
       'OP_CARRIER_FL_NUM_7432', 'OP_CARRIER_FL_NUM_7433',
       'OP_CARRIER_FL_NUM_7434', 'OP_CARRIER_FL_NUM_7435',
       'OP_CARRIER_FL_NUM_7436', 'OP_CARRIER_FL_NUM_7437',
       'OP_CARRIER_FL_NUM_7438', 'OP_CARRIER_FL_NUM_7439'],
      dtype='object', length=7135)

In [29]:
y = df_encoded[sorted(target_vars)].values

In [30]:
X = df_encoded[sorted(list(set(df_encoded.columns) - set(target_vars)))].values

In [31]:
X.shape

(105222, 7128)

In [32]:
import xgboost as xgb
from sklearn.model_selection import train_test_split

X_train, X_test, Y_train, Y_test = train_test_split(X, y, test_size=0.2, random_state = 42)

In [33]:
from sklearn import preprocessing
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import SGDRegressor, Ridge

In [34]:
#scaler = preprocessing.StandardScaler().fit(X_train)
scaler = preprocessing.MinMaxScaler().fit(X_train)

In [35]:
X_scaled = scaler.transform(X_train)

In [36]:
X_scaled

array([[0.56398499, 0.42317487, 0.3       , ..., 0.        , 0.        ,
        0.        ],
       [0.76823677, 0.72453311, 0.76666667, ..., 0.        , 0.        ,
        0.        ],
       [0.39766569, 0.34719864, 0.06666667, ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.44101709, 0.39685908, 0.76666667, ..., 0.        , 0.        ,
        0.        ],
       [0.84785327, 0.78395586, 0.4       , ..., 0.        , 0.        ,
        0.        ],
       [0.59274698, 0.44439728, 0.4       , ..., 0.        , 0.        ,
        0.        ]])

In [37]:
# reg = LinearRegression().fit(X_scaled, y=Y_train)

In [38]:
reg = Ridge(alpha=1.7).fit(X_scaled, y=Y_train)

In [39]:
reg.score(X_scaled, Y_train)

0.13357761253271766

In [40]:
X_test_scaled = scaler.transform(X_test)

In [41]:
reg.score(X_test_scaled, Y_test)

-0.0060240794015372

In [42]:
Y_predicted = reg.predict(X_test_scaled)

In [43]:
Y_predicted

array([[ 9.09684724e+00, -9.64886313e-01, -6.93845765e-01, ...,
         1.06400181e+01,  5.93395400e-01,  1.20609816e+00],
       [ 1.38958067e+01,  1.48759759e+01,  1.12358796e+01, ...,
         3.99106893e+00,  1.94597197e-01, -3.42406381e+00],
       [ 1.09270096e+02,  2.17969899e+01,  1.13487383e+02, ...,
         4.03828292e+01, -1.84817234e-01,  1.08139421e+00],
       ...,
       [ 3.87659529e+01, -4.62927960e-01,  2.87096016e+01, ...,
         4.03647969e+01,  1.98904923e-01, -4.80004824e+00],
       [ 6.86415719e+01,  1.83638465e+01,  6.85832430e+01, ...,
         1.06713089e+01,  3.20291035e-01, -2.69724763e+00],
       [ 4.51088243e+01,  1.89360086e+01,  4.00651820e+01, ...,
         1.33756390e+01,  8.31729920e-02,  5.47441723e+00]])

In [113]:
reg.coef_

array([[ 6.12102217, 15.26873904, -1.88204671, ..., -4.49704184,
        -2.17346662,  0.        ],
       [-8.88124159, -7.64755863,  1.73145289, ..., -7.19481358,
         8.21272971,  0.        ],
       [ 0.87327443, 29.65477749,  0.24368729, ..., -8.18742599,
        -2.10669382,  0.        ],
       ...,
       [ 7.85595849, -8.93940076, -3.00390619, ..., 11.42187269,
        -3.02683106,  0.        ],
       [-0.03798717,  0.05805815,  0.49969238, ...,  0.27979919,
         2.28530955,  0.        ],
       [ 0.8980447 ,  3.47820828, -2.26311448, ..., -3.42283431,
        -1.56959438,  0.        ]])

In [89]:
import m2cgen as m2c
import sys

In [90]:
sys.getrecursionlimit()

3000

In [93]:
sys.setrecursionlimit(100000)

In [94]:
m2c.export_to_c(reg)

KeyboardInterrupt: 

In [96]:
!pip3 install onnx skl2onnx

DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion at https://github.com/Homebrew/homebrew-core/issues/76621
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.2/12.2 MB 47.6 MB/s eta 0:00:00m eta 0:00:010:0101
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 278.1/278.1 kB 7.6 MB/s eta 0:00:00m eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.8/78.8 kB 6.7 MB/s eta 0:00:00
  DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion at https://github.com/Homebrew/homebrew-core/issues/76621
  DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion 

In [98]:
X_scaled.shape[1]

7128

In [ ]:
# Convert into ONNX format
from skl2onnx import convert_sklearn
from skl2onnx.common.data_types import FloatTensorType

In [ ]:
from skl2onnx import __max_supported_opset__
print("Last supported opset:", __max_supported_opset__)

In [116]:
# This requires python >= 3.7.

In [ ]:
initial_type = [('float_input', FloatTensorType([None, X_scaled.shape[1]]))]
onx = convert_sklearn(clr, initial_types=initial_type)
with open("model.onnx", "wb") as f:
    f.write(onx.SerializeToString())

In [72]:
from sklearn.metrics import mean_absolute_error

In [74]:
mean_absolute_error(Y_test, Y_predicted, multioutput='raw_values')

array([4.15907741e+10, 3.04502128e+10, 2.71152544e+10, 1.29126493e+10,
       1.55619486e+10, 1.09396865e+10, 5.39630281e+09])

In [55]:
Y_train

array([[28.,  0., -4., ..., 28.,  0.,  0.],
       [53.,  3., 54., ...,  0.,  0.,  0.],
       [43.,  0., 16., ..., 27.,  0.,  0.],
       ...,
       [53.,  0., 35., ..., 18.,  0.,  4.],
       [65.,  0., 40., ..., 25.,  0., 31.],
       [42.,  0., 49., ...,  0.,  0.,  0.]])

In [27]:
X_train.shape

(71552, 6214)

In [28]:
Y_train.shape

(71552, 7)

In [29]:
# following only works for newer XGBoost (> 1.6.0)

In [46]:
reg = xgb.XGBRegressor(verbosity=2,
                       eval_metric='mean_absolute_error',
                       num_target=Y_train.shape[1])

In [31]:
# older xgboost: train separate regressors...
#https://stackoverflow.com/questions/39540123/muti-output-regression-in-xgboost

In [32]:
from sklearn.multioutput import MultiOutputRegressor

In [35]:
multioutputregressor = MultiOutputRegressor(xgb.XGBRegressor(objective='reg:squarederror', 
                                                             verbosity=2,
                                                            )).fit(X_train, Y_train)


KeyboardInterrupt: 

In [ ]:
# squared error
print(np.mean((multioutputregressor.predict(X_test) - Y_test)**2, axis=0))

In [ ]:
!pip3 install xgboost>1.6.0

In [48]:
reg.fit(X_train, Y_train, eval_set=[(X_test, Y_test)])

ValueError: Invalid shape: (71552, 7) for label

In [40]:
D_train = xgb.DMatrix(X_train, label=Y_train)
D_test = xgb.DMatrix(X_test, label=Y_test)

ValueError: Invalid shape: (71552, 7) for label

In [ ]:
param = {
    'eta': 0.3, 
    'booster': 'gblinear',
    'verbosity':2
    'max_depth': 3,  
    'objective': 'multi:softprob',  
    'num_class': len(target_vars),
    'eval_metric': 'rmse'} 

steps = 20  # The number of training iterations

model = xgb.train(param, D_train, steps)

In [ ]:
import numpy as np
from sklearn.metrics import precision_score, recall_score, accuracy_score

preds = model.predict(D_test)
best_preds = np.asarray([np.argmax(line) for line in preds])

print("Precision = {}".format(precision_score(Y_test, best_preds, average='macro')))
print("Recall = {}".format(recall_score(Y_test, best_preds, average='macro')))
print("Accuracy = {}".format(accuracy_score(Y_test, best_preds)))

In [109]:
help(pd.get_dummies)

Help on function get_dummies in module pandas.core.reshape.reshape:

get_dummies(data, prefix=None, prefix_sep='_', dummy_na=False, columns=None, sparse=False, drop_first=False, dtype=None) -> 'DataFrame'
    Convert categorical variable into dummy/indicator variables.
    
    Parameters
    ----------
    data : array-like, Series, or DataFrame
        Data of which to get dummy indicators.
    prefix : str, list of str, or dict of str, default None
        String to append DataFrame column names.
        Pass a list with length equal to the number of columns
        when calling get_dummies on a DataFrame. Alternatively, `prefix`
        can be a dictionary mapping column names to prefixes.
    prefix_sep : str, default '_'
        If appending prefix, separator/delimiter to use. Or pass a
        list or dictionary as with `prefix`.
    dummy_na : bool, default False
        Add a column to indicate NaNs, if False NaNs are ignored.
    columns : list-like, default None
        Colu

In [107]:
df

QUARTER  MONTH  DAY_OF_MONTH  DAY_OF_WEEK OP_UNIQUE_CARRIER  \
0            2      6             5            4                XE   
1            2      6            12            4                XE   
2            2      6            16            1                XE   
3            2      6            18            3                XE   
4            2      6            23            1                XE   
...        ...    ...           ...          ...               ...   
89436        2      6             8            7                OO   
89437        2      6             9            1                OO   
89438        2      6             9            1                OO   
89439        2      6             9            1                OO   
89440        2      6             9            1                OO   

       OP_CARRIER_FL_NUM  ORIGIN_AIRPORT_ID  DEST_AIRPORT_ID  CRS_DEP_TIME  \
0                   2279              11049            12266          1655   
1                   2379              11049            12266          1655   
2                   2379              11049            12266          1655   
3                   2379              11049            12266          1655   
4                   2379              11049            12266          1655   
...                  ...                ...              ...           ...   
89436               6965              12892            14893          1300   
89437               3601              14869            14113          1855   
89438               3601              14113            14869          2015   
89439               3613              14869            15389          1845   
89440               3617              14869            15041          2010   

       DEP_DELAY  CRS_ARR_TIME  ARR_DELAY  DISTANCE  CARRIER_DELAY  \
0           42.0          1736       55.0      74.0            0.0   
1           26.0          1736       18.0      74.0            0.0   
2          118.0          1736      112.0      74.0            0.0   
3           -9.0          1736       17.0      74.0            0.0   
4           44.0          1736       39.0      74.0            0.0   
...          ...           ...        ...       ...            ...   
89436       20.0          1425       18.0     373.0           18.0   
89437       13.0          1947       30.0     150.0           30.0   
89438       19.0          2103       22.0     150.0           22.0   
89439        9.0          1941       21.0     175.0           21.0   
89440       20.0          2113       31.0     223.0           31.0   

       WEATHER_DELAY  NAS_DELAY  SECURITY_DELAY  LATE_AIRCRAFT_DELAY  
0                0.0       13.0             0.0                 42.0  
1                0.0        0.0             0.0                 18.0  
2                0.0        0.0             0.0                112.0  
3                0.0       17.0             0.0                  0.0  
4               39.0        0.0             0.0                  0.0  
...              ...        ...             ...                  ...  
89436            0.0        0.0             0.0                  0.0  
89437            0.0        0.0             0.0                  0.0  
89438            0.0        0.0             0.0                  0.0  
89439            0.0        0.0             0.0                  0.0  
89440            0.0        0.0             0.0                  0.0  

[89441 rows x 18 columns]

In [57]:
sorted(list(df.columns))

['ACTUAL_ELAPSED_TIME',
 'AIR_TIME',
 'ARR_DEL15',
 'ARR_DELAY',
 'ARR_DELAY_GROUP',
 'ARR_DELAY_NEW',
 'ARR_TIME',
 'ARR_TIME_BLK',
 'CANCELLATION_CODE',
 'CANCELLED',
 'CARRIER_DELAY',
 'CRS_ARR_TIME',
 'CRS_DEP_TIME',
 'CRS_ELAPSED_TIME',
 'DAY_OF_MONTH',
 'DAY_OF_WEEK',
 'DEP_DEL15',
 'DEP_DELAY',
 'DEP_DELAY_GROUP',
 'DEP_DELAY_NEW',
 'DEP_TIME',
 'DEP_TIME_BLK',
 'DEST',
 'DEST_AIRPORT_ID',
 'DEST_AIRPORT_SEQ_ID',
 'DEST_CITY_MARKET_ID',
 'DEST_CITY_NAME',
 'DEST_STATE_ABR',
 'DEST_STATE_FIPS',
 'DEST_STATE_NM',
 'DEST_WAC',
 'DISTANCE',
 'DISTANCE_GROUP',
 'DIV1_AIRPORT',
 'DIV1_AIRPORT_ID',
 'DIV1_AIRPORT_SEQ_ID',
 'DIV1_LONGEST_GTIME',
 'DIV1_TAIL_NUM',
 'DIV1_TOTAL_GTIME',
 'DIV1_WHEELS_OFF',
 'DIV1_WHEELS_ON',
 'DIV2_AIRPORT',
 'DIV2_AIRPORT_ID',
 'DIV2_AIRPORT_SEQ_ID',
 'DIV2_LONGEST_GTIME',
 'DIV2_TAIL_NUM',
 'DIV2_TOTAL_GTIME',
 'DIV2_WHEELS_OFF',
 'DIV2_WHEELS_ON',
 'DIV3_AIRPORT',
 'DIV3_AIRPORT_ID',
 'DIV3_AIRPORT_SEQ_ID',
 'DIV3_LONGEST_GTIME',
 'DIV3_TAIL_NUM',
 'DIV

In [1]:
!pip3 install xgboost

DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion at https://github.com/Homebrew/homebrew-core/issues/76621
     |████████████████████████████████| 1.7 MB 1.6 MB/s            
  DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion at https://github.com/Homebrew/homebrew-core/issues/76621
DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion at https://github.com/Homebrew/homebrew-core/issues/76621
You should consider upgrading via the '/usr/local/opt/python@3.9/bin/python3.9 -m pip install --upgrade pip' command.


In [2]:
from sklearn import datasets
import xgboost as xgb

In [3]:
iris = datasets.load_iris()
X = iris.data
y = iris.target

In [4]:
from sklearn.model_selection import train_test_split

X_train, X_test, Y_train, Y_test = train_test_split(X, y, test_size=0.2)

In [5]:
D_train = xgb.DMatrix(X_train, label=Y_train)
D_test = xgb.DMatrix(X_test, label=Y_test)

In [6]:
param = {
    'eta': 0.3, 
    'max_depth': 3,  
    'objective': 'multi:softprob',  
    'num_class': 3} 

steps = 20  # The number of training iterations

In [7]:
model = xgb.train(param, D_train, steps)

In [8]:
import numpy as np
from sklearn.metrics import precision_score, recall_score, accuracy_score

preds = model.predict(D_test)
best_preds = np.asarray([np.argmax(line) for line in preds])

print("Precision = {}".format(precision_score(Y_test, best_preds, average='macro')))
print("Recall = {}".format(recall_score(Y_test, best_preds, average='macro')))
print("Accuracy = {}".format(accuracy_score(Y_test, best_preds)))

Precision = 0.9326923076923078
Recall = 0.9326923076923078
Accuracy = 0.9333333333333333


In [9]:
from sklearn.model_selection import GridSearchCV

clf = xgb.XGBClassifier()
parameters = {
     "eta"    : [0.05, 0.10, 0.15, 0.20, 0.25, 0.30 ] ,
     "max_depth"        : [ 3, 4, 5, 6, 8, 10, 12, 15],
     "min_child_weight" : [ 1, 3, 5, 7 ],
     "gamma"            : [ 0.0, 0.1, 0.2 , 0.3, 0.4 ],
     "colsample_bytree" : [ 0.3, 0.4, 0.5 , 0.7 ]
     }

grid = GridSearchCV(clf,
                    parameters, n_jobs=4,
                    scoring="neg_log_loss",
                    cv=3)

grid.fit(X_train, Y_train)

GridSearchCV(cv=3,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None,
                                     early_stopping_rounds=None,
                                     enable_categorical=False, eval_metric=None,
                                     gamma=None, gpu_id=None, grow_policy=None,
                                     importance_type=None,
                                     interaction_constraints=None,
                                     learning_rate=None, max_bin=None,
                                     max_ca...
                                     missing=nan, monotone_constraints=None,
                                     n_estimators=100, n_jobs=None,
                                     num_parallel_tree=None, predictor=None,
                        

In [10]:
model.dump_model('dump.raw.txt')

In [11]:
!cat dump.raw.txt.raw.txtp.raw.txt

booster[0]:
0:[f2<2.5999999] yes=1,no=2,missing=1
	1:leaf=0.426589638
	2:leaf=-0.218769252
booster[1]:
0:[f2<2.5999999] yes=1,no=2,missing=1
	1:leaf=-0.213294834
	2:[f2<4.94999981] yes=3,no=4,missing=3
		3:[f3<1.60000002] yes=5,no=6,missing=5
			5:leaf=0.42281881
			6:leaf=-0.0620689802
		4:[f2<5.05000019] yes=7,no=8,missing=7
			7:leaf=-0.0360000096
			8:leaf=-0.21140942
booster[2]:
0:[f2<4.75] yes=1,no=2,missing=1
	1:leaf=-0.209708765
	2:[f2<4.94999981] yes=3,no=4,missing=3
		3:[f0<6.25] yes=5,no=6,missing=5
			5:leaf=0.128571421
			6:leaf=-7.66345476e-09
		4:leaf=0.409090936
booster[3]:
0:[f2<2.5999999] yes=1,no=2,missing=1
	1:leaf=0.294131458
	2:leaf=-0.195732966
booster[4]:
0:[f2<2.5999999] yes=1,no=2,missing=1
	1:leaf=-0.189599976
	2:[f3<1.54999995] yes=3,no=4,missing=3
		3:[f2<4.94999981] yes=5,no=6,missing=5
			5:leaf=0.292952508
			6:leaf=-0.1117642
		4:[f2<5.05000019] yes=7,no=8,missing=7
			7:leaf=-0.0383815542
			8:leaf=-0.187781304
booster[5]:
0:[f2<4.75] yes=1,no=2,missin